In [1]:
import json
import random
import numpy as np
import pandas as pd
import os

from bokeh.io import output_notebook, show
from bokeh.models import LogColorMapper
from bokeh.palettes import Viridis6 as palette
from bokeh_choropleth import *

In [2]:
palette.reverse()
output_notebook()

Loading BokehJS ...

In [3]:
def getRegiaoData(dataset, states):
    dataRegiao = pd.DataFrame()
    for state in states:
        dataRegiao = dataRegiao.append(dataset[dataset['UF'] == state])
    return dataRegiao

In [4]:
# read the data to a dataframe
data2017 = pd.read_csv('data/population_2017.csv')
data2017.columns = [cols.replace(' ', '_') for cols in data2017.columns]

nordeste = ['MA', 'PI', 'CE', 'RN', 'PB', 'PE','AL','SE', 'BA']



In [14]:
def carregar_geojson_ne():
    ne_geo_json = json.load(open('geojson/geojs-21-mun.json', encoding='latin-1'))

#     ne_geo_json['features'][112]['properties']['description'] = 'Serra Caiada'
#     ne_geo_json['features'][112]['properties']['name'] = 'Serra Caiada'

    for i in np.arange(2,10):
        ne_geo_json['features'] += (json.load(
            open(os.path.join('geojson', "geojs-2" + str(i) +  "-mun.json"),
                 encoding='latin-1')))['features']

    for feat in ne_geo_json['features']:
        if feat['properties']['description'] == 'Itapagé':
            feat['properties']['description'] = 'Itapajé'
        if feat['properties']['description'] == 'Quixabá':
            feat['properties']['description'] = 'Quixaba'
        if feat['properties']['description'] == 'Santarém':
            feat['properties']['description'] = 'Joca Claudino'
        if feat['properties']['description'] == 'Seridó':
            feat['properties']['description'] = 'São Vicente do Seridó'
        if feat['properties']['description'] == 'Campo de Santana':
            feat['properties']['description'] = 'Tacima'
        if feat['properties']['description'] == 'Belém de São Francisco':
            feat['properties']['description'] = 'Belém do São Francisco'
        if feat['properties']['description'] == 'Iguaraci':
            feat['properties']['description'] = 'Iguaracy'
        if feat['properties']['description'] == 'Gracho Cardoso':
            feat['properties']['description'] = 'Graccho Cardoso'
        if feat['properties']['description'] == 'Lagoa do Itaenga':
            feat['properties']['description'] = 'Lagoa de Itaenga'
        
    return ne_geo_json

def atualizar_geojson(geojson):
    for feat in geojson['features']:
        if feat['properties']['description'] == 'Itapagé':
            feat['properties']['description'] = 'Itapajé'
            feat['properties']['name'] = 'Itapajé'

        if feat['properties']['description'] == 'Quixabá':
            feat['properties']['description'] = 'Quixaba'
            feat['properties']['name'] = 'Quixaba'

        if feat['properties']['description'] == 'Santarém':
            feat['properties']['description'] = 'Joca Claudino'
            feat['properties']['name'] = 'Joca Claudino'

        if feat['properties']['description'] == 'Seridó':
            feat['properties']['description'] = 'São Vicente do Seridó'
            feat['properties']['name'] = 'São Vicente do Seridó'

        if feat['properties']['description'] == 'Campo de Santana':
            feat['properties']['description'] = 'Tacima'
            feat['properties']['name'] = 'Tacima'

        if feat['properties']['description'] == 'Belém de São Francisco':
            feat['properties']['description'] = 'Belém do São Francisco'
            feat['properties']['name'] = 'Belém do São Francisco'

        if feat['properties']['description'] == 'Iguaraci':
            feat['properties']['description'] = 'Iguaracy'
            feat['properties']['name'] = 'Iguaracy'

        if feat['properties']['description'] == 'Gracho Cardoso':
            feat['properties']['description'] = 'Graccho Cardoso'
            feat['properties']['name'] = 'Graccho Cardoso'

        if feat['properties']['description'] == 'Lagoa do Itaenga':
            feat['properties']['description'] = 'Lagoa de Itaenga'
            feat['properties']['name'] = 'Lagoa de Itaenga'

        if feat['properties']['id'] == 2410306:
            feat['properties']['description'] = 'Serra Caiada'
            feat['properties']['name'] = 'Serra Caiada'
            
    return geojson
    
def carregar_atualizar_geojson():
    return atualizar_geojson(carregar_geojson_ne())

def upper_name(geojson):
    for f in geojson['features']:
        f['properties']['name'] = f['properties']['name'].upper()
    return geojson
    
    

In [6]:
#População estimada na região nordeste

In [7]:
dataPopNE = (getRegiaoData(data2017, nordeste))
dataPopNE.columns = [cols.replace('POPULAÇÃO_ESTIMADA', 'POPULACAO_ESTIMADA',) for cols in dataPopNE.columns]
dataPopNE.columns = [cols.replace('NOME_DO_MUNICÍPIO', 'NOME_DO_MUNICIPIO',) for cols in dataPopNE.columns]

ne_geo = carregar_geojson_ne()


        
color_mapper = LogColorMapper(palette = palette, 
                              low=dataPopNE['POPULACAO_ESTIMADA'].min(), 
                              high=dataPopNE['POPULACAO_ESTIMADA'].max())

choropleth = bokeh_choropleth(data_df= dataPopNE,
                              geojson = ne_geo,
                              key_on = ['NOME_DO_MUNICIPIO', 'description'],
                              data = 'POPULACAO_ESTIMADA',
                              tooltips = [('UF', '@UF'), ('NOME_DO_MUNICIPIO', '@NOME_DO_MUNICIPIO'), ('POPULACAO_ESTIMADA', '@POPULACAO_ESTIMADA')],
                              color_mapper = color_mapper)
show(choropleth)

In [8]:
# Estimativa de tempo de espera por corrida uber, nos bairros da cidade de natal

In [9]:
# Time estimates

geo_json_natal = json.load(open('geojson/natal.geojson',encoding='UTF-8'))
estimativasData = pd.read_csv('data/estimates.csv', parse_dates=True, index_col=0)

estimativaMeanData = (estimativasData.pivot_table(index='Bairro',values='Tempo_espera')).reset_index()

In [10]:
color_mapper = LogColorMapper(palette = palette, 
                              low=estimativaMeanData['Tempo_espera'].min(), 
                              high=estimativaMeanData['Tempo_espera'].max())

choropleth = bokeh_choropleth(data_df= estimativaMeanData,
                              geojson = geo_json_natal,
                    key_on = ['Bairro', 'name'],
                              data = 'Tempo_espera',
                              tooltips = [('Bairro', '@Bairro'), ('Tempo_espera', '@Tempo_espera')],
                              color_mapper = color_mapper)
show(choropleth)

In [11]:
# Estimativa de preços do uber nos bairros da cidade de natal

In [12]:
geo_10_neibhorhood = json.load(open('geojson/bairros_sorteados.geojson',encoding='UTF-8'))

pricesData = pd.read_csv('data/prices.csv', names=
                         ['Tempo_coleta', 'Origem', 'Destino', 'Tipo_uber', 'Distancia', 
                          'High_price', 'Low_price', 'Duration', 'Estimate', 'Currency'])
pricesData['Mean_price'] = (pricesData['High_price'] + pricesData['Low_price'])/2.0
pricesMeanData = (pricesData.pivot_table(index='Destino', values='Mean_price', fill_value=0)).reset_index(level=0)


color_mapper = LogColorMapper(palette = palette, 
                              low=pricesMeanData['Mean_price'].min(), 
                              high=pricesMeanData['Mean_price'].max())

choropleth = bokeh_choropleth(data_df= pricesMeanData,
                              geojson = geo_10_neibhorhood,
                              key_on = ['Destino', 'name'],
                              data = 'Mean_price',
                              tooltips = [('Destino', '@Destino'), ('Mean_price', '@Mean_price')],
                              color_mapper = color_mapper)

show(choropleth)

In [ ]:
#Extras

In [ ]:
# Quantidade deFamilias atendidas pelo Bolsa Família

In [37]:
ne_bf_geojson = carregar_geojson_ne()
ne_bf_geojson = upper_name(ne_bf_geojson)
    
dataBF = pd.read_csv('data/BolsaFamilia2012.csv', encoding='latin-1') 
dataBF.columns = [cols.replace('uf', 'UF') for cols in dataBF.columns]


BFdataNordeste = getRegiaoData(dataBF, nordeste)
BFdataNordeste['nomemunici'] = BFdataNordeste['nomemunici'].str.replace('´', "'")
BFdataNordeste.at[1429,'nomemunici'] = 'SÃO DOMINGOS'
BFdataNordeste = BFdataNordeste.drop([1094])


In [26]:
color_mapper = LogColorMapper(palette = palette, 
                              low=BFdataNordeste['qtfamatend'].min(), 
                              high=BFdataNordeste['qtfamatend'].max())

choropleth = bokeh_choropleth(data_df= BFdataNordeste,
                              geojson = ne_bf_geojson,
                              key_on = ['nomemunici', 'name'],
                              data = 'qtfamatend',
                              tooltips = [('Nome do municipio', '@nomemunici'), ('Qtd famílias atend.', '@qtfamatend')],
                              color_mapper = color_mapper)

show(choropleth)

TypeError: Object of type 'int64' is not JSON serializable

In [39]:
#Quantidade de familias atendidas pelo CRAS

In [36]:
ne_cras_geojson = carregar_geojson_ne()
ne_cras_geojson = upper_name(ne_cras_geojson)

dataset_cras = os.path.join('data', 'AtendimentosCRAS.csv')
dataCras = pd.read_csv(dataset_cras, encoding='latin-1') 
dataCras.columns = [cols.replace('uf', 'UF') for cols in dataCras.columns]

dataCrasNordeste = getRegiaoData(dataCras, nordeste)

dataCrasNordeste['municipio'] = dataCrasNordeste['municipio'].str.replace('´', "'")
dataCrasNordeste.at[2883,'municipio'] = 'SÃO DOMINGOS'
dataCrasNordeste = dataCrasNordeste.drop(3166)



In [38]:
color_mapper = LogColorMapper(palette = palette, 
                              low=dataCrasNordeste['qtd_atend'].min(), 
                                  high=dataCrasNordeste['qtd_atend'].max())

choropleth = bokeh_choropleth(data_df= dataCrasNordeste,
                              geojson = ne_cras_geojson,
                              key_on = ['municipio', 'name'],
                              data = 'qtfamatend',
                              tooltips = [('Nome do municipio', '@municipio'), ('Qtd famílias atend.', '@qtd_atend')],
                              color_mapper = color_mapper)

show(choropleth)

TypeError: Object of type 'int64' is not JSON serializable